In [6]:
import pytesseract
import cv2
import pdf2image
import re
import pandas as pd
import os
from PIL import Image
import numpy as np

# Configurar caminho do Tesseract (caso necessário)
pytesseract.pytesseract.tesseract_cmd = r"C:\Program Files\Tesseract-OCR\tesseract.exe"

# Definir a variável de ambiente TESSDATA_PREFIX corretamente
os.environ['TESSDATA_PREFIX'] = r'C:\Program Files\Tesseract-OCR\tessdata'

def preprocessar_imagem(imagem_pil):
    """ Converte imagem para escala de cinza, aplica binarização e aumenta nitidez. """
    imagem_cv = np.array(imagem_pil)
    imagem_cv = cv2.cvtColor(imagem_cv, cv2.COLOR_RGB2GRAY)
    _, imagem_bin = cv2.threshold(imagem_cv, 150, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)
    return imagem_bin

def extrair_dados_pdf_ocr(caminho_pdf):
    """ Extrai e organiza os dados do PDF, segmentando por 'DESTINATÁRIO'. """
    paginas = pdf2image.convert_from_path(caminho_pdf)
    notas_fiscais = []
    sequencial = 1

    for i, pagina in enumerate(paginas):
        print(f"Processando página {i + 1}...")
        imagem_bin = preprocessar_imagem(pagina)
        texto = pytesseract.image_to_string(imagem_bin, lang="por", config="--psm 4 --oem 3")
        
        # Dividir o texto em blocos entre "DESTINATÁRIO"
        segmentos = re.split(r'DESTINATÁRIO', texto)

        for segmento in segmentos[1:]:  # Ignorar a parte antes do primeiro 'DESTINATÁRIO'
            # Armazenar os dados iniciais
            notas_fiscais.append({
                "Sequencial": sequencial,
                "Número da Nota Fiscal": "Não encontrado",  # Será preenchido depois
                "Valor Total da Nota Fiscal": "Não encontrado",  # Será preenchido depois
                "Texto Completo": segmento.strip()
            })
            sequencial += 1  # Incrementar o identificador

    df = pd.DataFrame(notas_fiscais)

    # **Varrer a coluna "Texto Completo" para extrair as informações corretas**
    for index, row in df.iterrows():
        texto = row["Texto Completo"]

        # Capturar qualquer número no formato 99.999,99 que não seja "0,000"
        valores_encontrados = re.findall(r'\b\d{1,3}(?:\.\d{3})*,\d{2}\b', texto)
        valores_filtrados = [v for v in valores_encontrados if v != "0,000"]

        if valores_filtrados:
            df.at[index, "Valor Total da Nota Fiscal"] = valores_filtrados[0]  # Pega o primeiro valor válido encontrado

        # Capturar um número de 5 dígitos cercado por espaços
        numero_nota_match = re.search(r'\s(\d{5})\s', texto)
        if numero_nota_match:
            df.at[index, "Número da Nota Fiscal"] = numero_nota_match.group(1).strip()

    # **Salvar o resultado em um arquivo CSV com ponto e vírgula como separador**
    
    # Criar um novo DataFrame sem a coluna "Texto Completo"
    df_limpo = df.drop(columns=["Texto Completo"])

    df_limpo.to_csv("resultado_notas_limpo.csv", sep=";", index=False, encoding="utf-8")
    print("Arquivo 'resultado_notas_limpo.csv' gerado com sucesso!")

    # df.to_csv("df.csv", sep=";", index=False, encoding="utf-8")
    # print("Arquivo 'df.csv' gerado com sucesso!")

    return df

# Exemplo de uso
caminho_pdf = "Notas_merged.pdf"  # Substituir pelo caminho correto do arquivo PDF
df_resultado = extrair_dados_pdf_ocr(caminho_pdf)

# Exibir o DataFrame com os resultados
# print(df_resultado)

# df_resultado.to_csv("df_resultado.csv", sep=";", index=False, encoding="utf-8")
# print("Arquivo 'df_resultado.csv' gerado com sucesso!")


Processando página 1...
Processando página 2...
Processando página 3...
Processando página 4...
Processando página 5...
Processando página 6...
Processando página 7...
Processando página 8...
Processando página 9...
Processando página 10...
Processando página 11...
Processando página 12...
Processando página 13...
Processando página 14...
Processando página 15...
Processando página 16...
Processando página 17...
Processando página 18...
Processando página 19...
Processando página 20...
Processando página 21...
Processando página 22...
Processando página 23...
Processando página 24...
Processando página 25...
Processando página 26...
Processando página 27...
Processando página 28...
Processando página 29...
Processando página 30...
Processando página 31...
Processando página 32...
Processando página 33...
Processando página 34...
Processando página 35...
Processando página 36...
Processando página 37...
Processando página 38...
Processando página 39...
Processando página 40...
Processan